## To identify the Best Players in Death over in IPL 2024

Importing required libraries
* We gratefully acknowledge **cricsheet.org** for providing the cricket statistics used in this analysis. Their comprehensive database was instrumental in compiling the data that enriches our understanding of the game.

In [1]:
import pandas as pd
import numpy as np
import math
import matplotlib.pyplot as plt

import warnings
warnings.filterwarnings('ignore')

pd.set_option('display.max_columns',None)
pd.set_option('display.expand_frame_repr',False)
pd.set_option('max_colwidth',-1)

* Downloaded data from cricsheet.org
* reading the data using read_csv()

In [2]:
data = pd.read_csv('ipl_csv2/all_matches.csv')

In [3]:
match_df = data.copy()

In [4]:
match_df.head(1)

match_id   season  start_date                  venue  innings  ball           batting_team                 bowling_team     striker  non_striker   bowler  runs_off_bat  extras  wides  noballs  byes  legbyes  penalty wicket_type player_dismissed  other_wicket_type  other_player_dismissed
0  335982    2007/08  2008-04-18  M Chinnaswamy Stadium  1        0.1   Kolkata Knight Riders  Royal Challengers Bangalore  SC Ganguly  BB McCullum  P Kumar  0             1      NaN    NaN      NaN    1.0     NaN       NaN         NaN             NaN                NaN

## Adding some more features to the data

In [5]:
match_df['isDot'] = match_df['runs_off_bat'] \
                        .apply(lambda x:1 if x==0 else 0)

match_df['isOne'] = match_df['runs_off_bat'] \
                        .apply(lambda x:1 if x==1 else 0)

match_df['isTwo'] = match_df['runs_off_bat'] \
                        .apply(lambda x:1 if x==2 else 0)

match_df['isThree'] = match_df['runs_off_bat'] \
                        .apply(lambda x:1 if x==3 else 0)

match_df['isFour'] = match_df['runs_off_bat'] \
                        .apply(lambda x:1 if x==4 else 0)

match_df['isSix'] = match_df['runs_off_bat'] \
                        .apply(lambda x:1 if x==6 else 0)

match_df['isBoundary'] = match_df['runs_off_bat'] \
                            .apply(lambda x:1 if x==6 or x==4 else 0)

match_df['Over'] = match_df['ball'] \
                    .apply(lambda x:math.floor(x)+1)

match_df['year']=pd.to_datetime(match_df['start_date']).dt.year


In [6]:
match_df.tail(2)

match_id season  start_date                                     venue  innings  ball  batting_team         bowling_team         striker     non_striker      bowler  runs_off_bat  extras  wides  noballs  byes  legbyes  penalty wicket_type player_dismissed  other_wicket_type  other_player_dismissed  isDot  isOne  isTwo  isThree  isFour  isSix  isBoundary  Over  year
255757  1426287   2024   2024-05-01  MA Chidambaram Stadium, Chepauk, Chennai  2        17.5  Punjab Kings  Chennai Super Kings  SM Curran       Shashank Singh  RJ Gleeson  0             1      NaN    NaN      NaN    1.0     NaN       NaN         NaN             NaN                NaN                      1      0      0      0        0       0      0           18    2024
255758  1426287   2024   2024-05-01  MA Chidambaram Stadium, Chepauk, Chennai  2        17.6  Punjab Kings  Chennai Super Kings  Shashank Singh  SM Curran       RJ Gleeson  2             0      NaN    NaN      NaN   NaN      NaN       NaN         NaN             NaN                NaN                      0      0      1      0        0       0      0           18    2024

### Filtering the data Selecting only Death overs and IPL season 2024

In [7]:
match_df= match_df[(match_df['Over']>16)&(match_df['year']==2024)]

In [8]:
pd.DataFrame(match_df.groupby(['striker'])['runs_off_bat'].sum()).head(4)

runs_off_bat
striker                 
A Badoni    69          
A Nortje    3           
AD Russell  89          
AJ Turner   1

In [9]:
runs = pd.DataFrame(match_df \
                    .groupby(['striker'])['runs_off_bat'].sum()) \
                    .sort_values(by=['runs_off_bat'],ascending=False) \
                    .reset_index() \
                    .rename(columns={'runs_off_bat':'Runs'})

In [10]:
balls = pd.DataFrame(match_df[pd.isnull(match_df['wides'])] \
                    .groupby(['striker'])['Over'].count()) \
                    .sort_values(by=['striker'],ascending=False) \
                    .reset_index() \
                    .rename(columns={'Over':'Balls faced'})

In [11]:
innings = pd.DataFrame(match_df \
                    .groupby(['striker'])['match_id']\
                    .apply(lambda x:len(list(np.unique(x))))) \
                    .sort_values(by=['striker'],ascending=False)\
                    .reset_index() \
                    .rename(columns={'match_id':'innings'})

In [12]:
dismissals = pd.DataFrame(match_df \
                    .groupby(['striker'])['player_dismissed'].count()) \
                    .sort_values(by=['striker'],ascending=False) \
                    .reset_index() \
                    .rename(columns={'player_dismissed':'dismissals'})

In [13]:
sixes = pd.DataFrame(match_df \
                    .groupby(['striker'])['isSix'].sum()) \
                    .sort_values(by=['striker'],ascending=False) \
                    .reset_index() \
                    .rename(columns={'isSix':'Sixes'})

In [14]:
fours = pd.DataFrame(match_df \
                    .groupby(['striker'])['isFour'].sum()) \
                    .sort_values(by=['striker'],ascending=False)\
                    .reset_index() \
                    .rename(columns={'isFour':'Fours'})

#### Merging all the dataframes to combine all the required attributes

In [15]:
merge_df = pd.merge(innings,runs, on='striker') \
                    .merge(balls, on='striker') \
                    .merge(dismissals, on='striker') \
                    .merge(sixes, on='striker') \
                    .merge(fours, on='striker')

### Adding more attributes to identify the best player

In [16]:
merge_df['Strike Rate']= 100*merge_df['Runs']/merge_df['Balls faced']
merge_df['RPI']= merge_df['Runs']/merge_df['innings']
merge_df['Average']= merge_df['Runs']/merge_df['dismissals']
merge_df['Boundary']= merge_df['Sixes']+merge_df['Fours']
merge_df['Boundary percentage']= merge_df['Boundary']/merge_df['Balls faced']*100
merge_df['Balls per boundary']= merge_df['Balls faced']/merge_df['Boundary']

#### Minimum 2 innings played in death overs

In [17]:
df_death_over=merge_df[(merge_df['innings']>2)] \
                .sort_values(by='Strike Rate', ascending=False) \
                .reset_index() \
                .head(10)

### Storing the data in csv file

In [18]:
df_death_over.to_csv("Death overs.csv")

In [19]:
df_death_over = df_death_over.drop('index',axis=1)

In [20]:
df_death_over[['striker',
               'innings',
               'Runs',
               'Boundary',
               'Boundary percentage',
               'Strike Rate']].head(6)

striker  innings  Runs  Boundary  Boundary percentage  Strike Rate
0  T Stubbs    5        152   24        46.153846            292.307692 
1  R Shepherd  4        56    10        50.000000            280.000000 
2  SS Iyer     5        63    10        41.666667            262.500000 
3  H Klaasen   4        107   16        38.095238            254.761905 
4  R Parag     3        59    9         37.500000            245.833333 
5  RR Pant     4        88    14        38.888889            244.444444